# RelationalAI Native App Cost Monitoring

Using RelationalAI (RAI) on Snowflake incurs costs from both Snowflake and RAI itself. Snowflake costs are based on compute and storage resource usage, detailed in the [Snowflake User Guide](https://docs.snowflake.com/en/guides-overview-cost).

RAI costs include a surcharge for compute usage, primarily from RAI engines. There’s no surcharge for storage used by the application. Similar to Snowflake, RAI’s cloud architecture separates storage and compute usage, allowing for cost optimization based on specific needs. For more information, please visit [the RelationalAI website](https://relational.ai/docs/manage/costs).

> :warning: Before the end of 2024, Snowflake will add support for detailed cost monitoring of their native apps within the standard Snowflake cost monitoring tools. In the meantime, this notebook can be used to get an understanding of the number of units that are used by RAI engines. You can also use these queries in Snowflake Dashboards to visualize the estimated RAI units used.



## List Active Engines

This query lists all the RAI engines that are currently running in the account:


In [ ]:
SELECT * FROM relationalai.api.engines;

## Show Total Number Of RAI Units By Month

This query provides the total number of RAI units used by RAI engines for the past month:


In [ ]:
SELECT
  DATE_TRUNC('MONTH', hour) AS first_day_of_month,
  SUM(credits) AS sum_of_rai_units
FROM
  relationalai.consumption.engine_credit_hours
GROUP BY
  first_day_of_month
ORDER BY
  first_day_of_month DESC;

## Snow Number Of RAI Units Used By Day

This query provides a daily breakdown of the total number of RAI units used by RAI engines for the past month.


In [ ]:
SELECT
  DATE_TRUNC('day',c.HOUR) as day, sum(c.credits) AS total_daily_rai_units
FROM
  relationalai.consumption.engine_credit_hours c
WHERE
  hour >= DATEADD(month, -1, CURRENT_TIMESTAMP())
GROUP BY all ORDER BY 1 DESC;

## Show Number Of RAI Units Used By Engine

This query provides an breakdown by RAI engine of the total number of RAI units used during the past month.

Note that if an engine with a certain name was created by multiple people during the selected period, the name in the `user_name` column reflects the name of the last user who created the engine.


In [ ]:
WITH engine_ownership AS (
    SELECT DISTINCT
        REPLACE(REPLACE(REGEXP_SUBSTR(QUERY_TEXT, $$'.*',$$, 1, 1, 'e'), '\'',''), ',','') AS engine_name,
        max(USER_NAME) AS user_name
    FROM
        SNOWFLAKE.ACCOUNT_USAGE.QUERY_HISTORY
    WHERE
        QUERY_TEXT ILIKE '%create_engine%'
        AND start_time >= DATEADD(month, -1, CURRENT_TIMESTAMP())
    GROUP BY engine_name
)
SELECT
    c.engine_name,
    o.user_name,
    sum(c.credits) AS total_rai_units_by_engine
FROM
    relationalai.consumption.engine_credit_hours c
INNER JOIN
    engine_ownership o ON c.engine_name = o.engine_name
WHERE
    hour >= DATEADD(month, -1, CURRENT_TIMESTAMP())
GROUP BY 1, 2 ORDER BY 3 DESC;

## Compute Pools Cost For the RAI Native App

Your account incurs compute costs from two main sources when the RAI Native App is installed:

- Central Service Compute Pool: Allocated to the native app for RelationalAI service operations, without any RAI compute surcharge. The RAI service compute pool is created automatically when the app is activated, and suspended automatically when the app is deactivated.
- Engine Compute Pools: Used to query RAI models. Like Snowflake virtual warehouses, engines can be independently created for workload isolation or scaling. These pools have a RAI cost surcharge based on their uptime. RAI Engines are managed through the RelationalAI CLI or provided SQL procedures (see queries above for engine uptimes).


In [ ]:
SELECT
    DATE_TRUNC('MONTH', START_TIME) AS first_day_of_month,
    compute_pool_name,
    SUM(credits_used) as total_credits
FROM
   SNOWFLAKE.ACCOUNT_USAGE.SNOWPARK_CONTAINER_SERVICES_HISTORY
WHERE
    APPLICATION_NAME = 'RELATIONALAI'
GROUP BY
    first_day_of_month, compute_pool_name
ORDER BY
    first_day_of_month DESC,
    compute_pool_name;

## Compute Warehouse Costs For the RAI Native App

The RAI Native App utilizes a Snowflake virtual warehouse for Snowflake interoperability. This warehouse is created automatically when the RAI application is activated, and suspended automatically when the app is deactivated. There’s no RAI cost surcharge for using the virtual warehouse.


In [ ]:
SELECT
    DATE_TRUNC('MONTH', START_TIME) AS first_day_of_month,
    SUM(credits_used) as total_credits
FROM
    SNOWFLAKE.ACCOUNT_USAGE.WAREHOUSE_METERING_HISTORY
WHERE
    WAREHOUSE_NAME = 'RELATIONAL_AI_ERP_WAREHOUSE'
GROUP BY
  first_day_of_month
ORDER BY
  first_day_of_month DESC